In [36]:
import pandas as pd
import random
import joblib
from tensorflow.keras.models import load_model
from features import extract_sequence, fixed_length

In [37]:
dftp = pd.read_csv("timestampsDatetimeA.csv", header=None, names=range(231))
dftp.head()

C:\Users\maxbr\AppData\Local\Temp\ipykernel_6284\993521357.py:1: DtypeWarning: Columns (206,207,208,209,210,211,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230) have mixed types. Specify dtype option on import or set low_memory=False.
  dftp = pd.read_csv("timestampsDatetimeA.csv", header=None, names=range(231))


0                                        1           2    \
0              fighter                                    event        date   
1   Mansur Abdul-Malik                                      UFC  2025-02-23   
2           Daichi Abe  UFC Fight Night 132: Cowboy vs. Edwards  2018-06-23   
3          John Adajar                            Road to UFC 4  2022-06-10   
4  Shamil Abdurakhimov                                  UFC 283  2023-01-21   

               3                                  4    \
0         opponent                         timestep-1   
1       Nick Klein  2025-02-13 14:17:00 - price: -549   
2     Li Jingliang  2018-06-13 12:09:00 - price: +240   
3     Han Seul Kim  2022-06-07 10:00:00 - price: -120   
4  Jailton Almeida  2023-01-06 10:00:00 - price: +600   

                                 5                                  6    \
0                         timestep-2                         timestep-3   
1  2025-02-13 20:33:00 - price: -549  2025-02-14 18:09:00 - price: -562   
2  2018-06-13 12:21:00 - price: +325  2018-06-13 13:42:00 - price: +315   
3  2022-06-07 10:18:00 - price: +105  2022-06-07 22:02:00 - price: -105   
4  2023-01-06 13:20:00 - price: +583  2023-01-07 19:48:00 - price: +588   

                                 7                                  8    \
0                         timestep-4                         timestep-5   
1  2025-02-14 18:13:00 - price: -532  2025-02-14 19:09:00 - price: -569   
2  2018-06-13 15:24:00 - price: +323  2018-06-13 16:18:00 - price: +320   
3  2022-06-08 13:08:00 - price: +100  2022-06-08 13:26:00 - price: +115   
4  2023-01-08 15:40:00 - price: +585  2023-01-08 23:16:00 - price: +593   

                                 9    ...           221           222  \
0                         timestep-6  ...  timestep-218  timestep-219   
1  2025-02-14 19:11:00 - price: -569  ...           NaN           NaN   
2  2018-06-13 17:06:00 - price: +313  ...           NaN           NaN   
3  2022-06-08 13:50:00 - price: +118  ...           NaN           NaN   
4  2023-01-08 23:54:00 - price: +596  ...           NaN           NaN   

            223           224           225           226           227  \
0  timestep-220  timestep-221  timestep-222  timestep-223  timestep-224   
1           NaN           NaN           NaN           NaN           NaN   
2           NaN           NaN           NaN           NaN           NaN   
3           NaN           NaN           NaN           NaN           NaN   
4           NaN           NaN           NaN           NaN           NaN   

            228           229           230  
0  timestep-225  timestep-226  timestep-227  
1           NaN           NaN           NaN  
2           NaN           NaN           NaN  
3           NaN           NaN           NaN  
4           NaN           NaN           NaN  

[5 rows x 231 columns]

In [38]:
dftp.columns = dftp.iloc[0]
dftp = dftp[1:]
dftp.reset_index(drop=True, inplace=True)
dftp.head()

0              fighter                                    event        date  \
0   Mansur Abdul-Malik                                      UFC  2025-02-23   
1           Daichi Abe  UFC Fight Night 132: Cowboy vs. Edwards  2018-06-23   
2          John Adajar                            Road to UFC 4  2022-06-10   
3  Shamil Abdurakhimov                                  UFC 283  2023-01-21   
4     Hamdy Abdelwahab                                      UFC  2025-02-01   

0         opponent                         timestep-1  \
0       Nick Klein  2025-02-13 14:17:00 - price: -549   
1     Li Jingliang  2018-06-13 12:09:00 - price: +240   
2     Han Seul Kim  2022-06-07 10:00:00 - price: -120   
3  Jailton Almeida  2023-01-06 10:00:00 - price: +600   
4     Jamal Pogues  2025-01-14 07:53:00 - price: +105   

0                         timestep-2                         timestep-3  \
0  2025-02-13 20:33:00 - price: -549  2025-02-14 18:09:00 - price: -562   
1  2018-06-13 12:21:00 - price: +325  2018-06-13 13:42:00 - price: +315   
2  2022-06-07 10:18:00 - price: +105  2022-06-07 22:02:00 - price: -105   
3  2023-01-06 13:20:00 - price: +583  2023-01-07 19:48:00 - price: +588   
4  2025-01-14 12:39:00 - price: +113  2025-01-15 08:41:00 - price: +110   

0                         timestep-4                         timestep-5  \
0  2025-02-14 18:13:00 - price: -532  2025-02-14 19:09:00 - price: -569   
1  2018-06-13 15:24:00 - price: +323  2018-06-13 16:18:00 - price: +320   
2  2022-06-08 13:08:00 - price: +100  2022-06-08 13:26:00 - price: +115   
3  2023-01-08 15:40:00 - price: +585  2023-01-08 23:16:00 - price: +593   
4  2025-01-16 12:13:00 - price: +111  2025-01-16 14:27:00 - price: +111   

0                         timestep-6  ... timestep-218 timestep-219  \
0  2025-02-14 19:11:00 - price: -569  ...          NaN          NaN   
1  2018-06-13 17:06:00 - price: +313  ...          NaN          NaN   
2  2022-06-08 13:50:00 - price: +118  ...          NaN          NaN   
3  2023-01-08 23:54:00 - price: +596  ...          NaN          NaN   
4  2025-01-16 15:57:00 - price: +112  ...          NaN          NaN   

0 timestep-220 timestep-221 timestep-222 timestep-223 timestep-224  \
0          NaN          NaN          NaN          NaN          NaN   
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4          NaN          NaN          NaN          NaN          NaN   

0 timestep-225 timestep-226 timestep-227  
0          NaN          NaN          NaN  
1          NaN          NaN          NaN  
2          NaN          NaN          NaN  
3          NaN          NaN          NaN  
4          NaN          NaN          NaN  

[5 rows x 231 columns]

In [39]:
df = pd.read_csv('simData48Clean.csv')
df.head()

date event          fighter1                    fighter1 - open  \
0  2025-03-09   UFC    Curtis Blaydes  2025-01-18 02:57:00 - price: -275   
1  2025-03-09   UFC   Brunno Ferreira  2025-02-24 18:07:00 - price: +105   
2  2025-03-09   UFC     Rafael Fiziev  2025-02-27 05:11:00 - price: -139   
3  2025-03-09   UFC  Francis Marshall  2025-02-24 18:15:00 - price: +290   
4  2025-03-09   UFC    John Castaneda  2025-03-03 09:01:00 - price: -112   

                      fighter1 - 48h                   fighter1 - close  \
0  2025-03-06 15:01:00 - price: -339  2025-03-08 15:01:00 - price: -335   
1  2025-03-06 21:01:00 - price: +116  2025-03-08 21:01:00 - price: +112   
2  2025-03-07 01:01:00 - price: -163  2025-03-08 23:01:00 - price: -159   
3  2025-03-06 17:01:00 - price: +247  2025-03-08 19:01:00 - price: +197   
4  2025-03-06 15:01:00 - price: -106  2025-03-08 15:01:00 - price: -108   

          fighter2                    fighter2 - open  \
0    Rizvan Kuniev  2025-01-18 02:57:00 - price: +210   
1  Armen Petrosyan  2025-02-24 18:07:00 - price: -125   
2   Justin Gaethje  2025-02-27 05:11:00 - price: +112   
3    Mairon Santos  2025-02-24 18:15:00 - price: -370   
4  Chris Gutierrez  2025-03-03 09:01:00 - price: -112   

                      fighter2 - 48h                   fighter2 - close  \
0  2025-03-06 15:01:00 - price: +259  2025-03-08 15:01:00 - price: +261   
1  2025-03-06 21:01:00 - price: -141  2025-03-08 21:01:00 - price: -134   
2  2025-03-07 01:01:00 - price: +133  2025-03-08 23:01:00 - price: +131   
3  2025-03-06 17:01:00 - price: -322  2025-03-08 19:01:00 - price: -245   
4  2025-03-06 15:01:00 - price: -116  2025-03-08 15:01:00 - price: -112   

            winner  
0              NaN  
1  Brunno Ferreira  
2   Justin Gaethje  
3    Mairon Santos  
4              NaN

In [40]:
print(df.isna().any(axis=1).sum())
df = df.dropna().reset_index(drop=True)
print(df.isna().any(axis=1).sum())

285
0


In [41]:
def calculate_profit(wager, price):
    if price > 0:
        profit = (price/100)*wager
    else:
        profit = (100/abs(price))*wager
    return profit

In [42]:

def perform_sim(wager, model, input_size, input_type):
    bankroll = wager * len(df)

    profit_dict = {
        'favorite_at_open': bankroll,
        'favorite_at_48': bankroll,
        'favorite_at_close': bankroll,
        'favorite_random': bankroll,
        'favorite_top_bound': bankroll,
        'favorite_ML': bankroll,
        'favorite_low_bound':bankroll,
        

        'underdog_at_open': bankroll, 
        'underdog_at_48': bankroll,
        'underdog_at_close': bankroll,
        'underdog_random': bankroll,
        'underdog_top_bound': bankroll,
        'underdog_ML': bankroll,
        'underdog_low_bound': bankroll,

        'true_random': bankroll
    }

    for index, row in df.iterrows():
        fighter1 = row['fighter1']
        fighter2 = row['fighter2']
        winner = row['winner']

        #get open line
        open1 = int(row['fighter1 - open'].split('price: ')[1])
        open2 = int(row['fighter2 - open'].split('price: ')[1])

        #get 48h lines
        forty81 = int(row['fighter1 - 48h'].split('price: ')[1])
        forty82 = int(row['fighter2 - 48h'].split('price: ')[1])

        #get closing lines
        close1 = int(row['fighter1 - close'].split('price: ')[1])
        close2 = int(row['fighter2 - close'].split('price: ')[1])

        lines = {
            fighter1: [open1, forty81, close1],
            fighter2: [open2, forty82, close2]
        }

        true_random_fighter = random.choice([fighter1, fighter2])
        true_random = lines[true_random_fighter][random.randint(0,2)]

        if true_random_fighter == winner:
            profit_dict['true_random']+=calculate_profit(wager, true_random)
        else:
            profit_dict['true_random']-=wager



        #find who is favorite and dog at open
        if open1<open2:
            fav_at_open = fighter1
            dog_at_open = fighter2
        elif open2<open1:
            fav_at_open = fighter2
            dog_at_open = fighter1
        else:
            #if lines are dead even randomly pick a fighter
            fav_at_open = random.choice([fighter1, fighter2])
            if fav_at_open == fighter1:
                dog_at_open = fighter2
            else:
                dog_at_open = fighter1

        if fav_at_open == winner:
            profit_dict['favorite_at_open']+=calculate_profit(wager, lines[winner][0])
            profit_dict['underdog_at_open']-=wager
        elif dog_at_open == winner:
            profit_dict['underdog_at_open']+=calculate_profit(wager, lines[winner][0])
            profit_dict['favorite_at_open']-=wager



        #get favorite at 48 and dog at 48
        if forty81<forty82:
            fav_at_48 = fighter1
            dog_at_48 = fighter2
        elif forty82<forty81:
            fav_at_48 = fighter2
            dog_at_48 = fighter1
        else:
            fav_at_48 = random.choice([fighter1, fighter2])
            if fav_at_48 == fighter1:
                dog_at_48 = fighter2
            else:
                dog_at_48 = fighter1


        #fav_at_48 and dog_at_48 then pick random between closing and 
        fav_random = random.randint(1,2)
        dog_random = random.randint(1,2)

        #randomly choose open or close
        fav_random_line = lines[fav_at_48][fav_random]
        dog_random_line = lines[dog_at_48][dog_random]

        fav_lines = lines[fav_at_48]
        dog_lines = lines[dog_at_48]

        if fav_lines[1] > fav_lines[2]:
            fav_top_bound = fav_lines[1]
            fav_low_bound = fav_lines[2]
        else:
            fav_top_bound = fav_lines[2]
            fav_low_bound = fav_lines[1]

        if dog_lines[1] > dog_lines[2]:
            dog_top_bound = dog_lines[1]
            dog_low_bound = dog_lines[2]
        else:
            dog_top_bound = dog_lines[2]
            dog_low_bound = dog_lines[1]


        #find the sequence
        fav_frame = dftp[(dftp['fighter'] == fav_at_48) 
                    & (dftp['opponent'] == dog_at_48)
                    & (dftp['date'] == row['date'])]
        
        dog_frame = dftp[(dftp['fighter'] == dog_at_48) 
                    & (dftp['opponent'] == fav_at_48)
                    & (dftp['date'] == row['date'])]
        
        #extract sequences
        fav_sequence = extract_sequence(fav_frame)
        dog_sequence = extract_sequence(dog_frame)

        #generate input data
        fav_seq = fixed_length(fav_sequence, input_size, 'linear')
        dog_seq = fixed_length(dog_sequence, input_size, 'linear')

        fav_action = model.predict([fav_seq])[0]
        dog_action = model.predict([dog_seq])[0]

        fav_ML = lines[fav_at_48][fav_action+1]
        dog_ML = lines[dog_at_48][dog_action+1]
        
        if fav_at_48 == winner:
            profit_dict['favorite_at_48']+=calculate_profit(wager, lines[winner][1])
            profit_dict['favorite_random']+=calculate_profit(wager, fav_random_line)
            profit_dict['favorite_top_bound']+=calculate_profit(wager, fav_top_bound)
            profit_dict['favorite_low_bound']+=calculate_profit(wager, fav_low_bound)
            profit_dict['favorite_ML']+=calculate_profit(wager, fav_ML)
            profit_dict['underdog_at_48']-=wager
            profit_dict['underdog_random']-=wager
            profit_dict['underdog_top_bound']-=wager
            profit_dict['underdog_low_bound']-=wager
            profit_dict['underdog_ML']-=wager
        elif dog_at_48 == winner:
            profit_dict['underdog_at_48']+=calculate_profit(wager, lines[winner][1])
            profit_dict['underdog_random']+=calculate_profit(wager, dog_random_line)
            profit_dict['underdog_top_bound']+=calculate_profit(wager, dog_top_bound)
            profit_dict['underdog_low_bound']+=calculate_profit(wager, dog_low_bound)
            profit_dict['underdog_ML']+=calculate_profit(wager, dog_ML)
            profit_dict['favorite_at_48']-=wager
            profit_dict['favorite_random']-=wager
            profit_dict['favorite_top_bound']-=wager
            profit_dict['favorite_low_bound']-=wager
            profit_dict['favorite_ML']-=wager

        if close1<close2:
            fav_at_close=fighter1
            dog_at_close = fighter2
        elif close2<close1:
            fav_at_close=fighter2
            dog_at_close = fighter1
        else:
            fav_at_close = random.choice([fighter1, fighter2])
            if fav_at_close == fighter1:
                dog_at_close = fighter2
            else:
                dog_at_close = fighter1

        if fav_at_close == winner:
            profit_dict['favorite_at_close']+=calculate_profit(wager, lines[winner][2])
            profit_dict['underdog_at_close']-=wager
        elif dog_at_close == winner:
            profit_dict['underdog_at_close']+=calculate_profit(wager, lines[winner][2])
            profit_dict['favorite_at_close']-=wager


        


    for k in profit_dict:
            profit_dict[k] = (profit_dict[k] - bankroll) / bankroll

    return profit_dict           


In [43]:
regression = joblib.load('regression.pkl')

In [44]:
regressionSim = perform_sim(100, regression, 20, 'none')

c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.apply

In [45]:
print(regressionSim)

{'favorite_at_open': -0.035369349602049266, 'favorite_at_48': -0.025739063766029784, 'favorite_at_close': -0.02470010445071335, 'favorite_random': -0.02458992194092956, 'favorite_top_bound': -0.006236165771723507, 'favorite_ML': -0.023934616168569615, 'favorite_low_bound': -0.044723472921633776, 'underdog_at_open': -0.11136832815927529, 'underdog_at_48': -0.0940067078293534, 'underdog_at_close': -0.08368988028094179, 'underdog_random': -0.08949918600950242, 'underdog_top_bound': -0.053978830319861226, 'underdog_ML': -0.08191276937759068, 'underdog_low_bound': -0.12319728731381982, 'true_random': -0.055213169177256514}


In [46]:
regression100 = joblib.load('regression100.pkl')

In [47]:
regression100sim = perform_sim(100, regression100, 100, 'none')

c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  frame = frame.applymap(lambda x: x.split(' - price: ')[1].strip()
c:\Users\maxbr\OneDrive\Desktop\CLVSim\CLVSim\CLV Sim\Sim\features.py:65: FutureWarning: DataFrame.apply

In [48]:
print(regression100sim)

{'favorite_at_open': -0.03284538083486493, 'favorite_at_48': -0.027949936043593217, 'favorite_at_close': -0.02619155557871719, 'favorite_random': -0.02833857847769496, 'favorite_top_bound': -0.008681534097226464, 'favorite_ML': -0.02579619301027902, 'favorite_low_bound': -0.04683971493526602, 'underdog_at_open': -0.11389229692645962, 'underdog_at_48': -0.09179583555178997, 'underdog_at_close': -0.08219842915293796, 'underdog_random': -0.08620148269743697, 'underdog_top_bound': -0.051533461994358265, 'underdog_ML': -0.07986623193143952, 'underdog_low_bound': -0.12108104530018757, 'true_random': -0.07211755203622278}
